In [38]:
import cv2 as cv
import numpy as np
import matplotlib.pyplot as plt
import copy
import os

In [39]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [40]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int
  prev_point_missing: bool
  open_ending: bool

In [41]:
def peeling(img):
  img2 = img
  prev_img = img2
  kernel = np.ones((3,3),np.uint8)
  maxsteps = 100
  while np.max(np.max(img2))>0 and maxsteps>0:
    prev_img = img2
    img2 = cv.morphologyEx(img2, cv.MORPH_ERODE, kernel)
    maxsteps = maxsteps-1
  
  #Centre of mass on the skeletonized image
  M = cv.moments(prev_img)
  cX = int(M["m10"] / M["m00"])
  cY = int(M["m01"] / M["m00"])
  centre = [cX,cY]

  return centre

In [42]:
#Setting up parameters

out_path = '/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Path estimation/Outputs/v3/'

MaxFrame = 50
movementlimit = 50

MaxTracebackDist = 70
MaxTraceback = 3
TracebackCooldown = 5

TrackedIDs = [9,5,6,44,35,15]

In [43]:
#Setting up video writing

cap = cv.VideoCapture('/content/drive/My Drive/Colab Notebooks/CellTracking/Inputs/input2.avi')
ret, frame1 = cap.read()
prvs = cv.cvtColor(frame1,cv.COLOR_BGR2GRAY)
hsv = np.zeros_like(frame1)
hsv[...,1] = 255

#FRAME 2
picture_number=1
row=1

#Video Write object
frame_width=int(cap.get(3))
frame_height=int(cap.get(4))

#out_tresholded = cv.VideoWriter(out_path + 'v_2_0_tresholded.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
#out_opened = cv.VideoWriter(out_path + 'v_2_0_opened.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
out_centres = cv.VideoWriter(out_path + 'v3_centres.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
out_movements = cv.VideoWriter(out_path + 'v3_movements.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
out_single_cell = cv.VideoWriter(out_path + 'v3_marked_cells.avi', cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))

#Starting the analysis

Centres = []
AllCentres = []
AllPrevCentres = []
AllPaths = []
NewCellID = 0

FrameCounter = 0
ret, frame2 = cap.read()

while(ret and FrameCounter<MaxFrame):
    print(FrameCounter)
    
    next1 = cv.cvtColor(frame2,cv.COLOR_BGR2GRAY)
    
    H,W = next1.shape
    
    ############ SAJAT
    
    #------------ Preprocessing ------------

    tresh = ((1-(next1 < 150)*(next1>100))*255).astype(np.uint8)  #band cut treshold
    #ret0, tresh = cv.threshold(next1,100,255,cv.THRESH_BINARY)
    
    closing_kernel = np.ones((10,10),np.uint8)
    opening_kernel = np.ones((4,4),np.uint8)
    
    closed = cv.morphologyEx(tresh, cv.MORPH_CLOSE, closing_kernel)
    opened = cv.morphologyEx(closed, cv.MORPH_OPEN, opening_kernel)
    opened = cv.morphologyEx(opened, cv.MORPH_OPEN, opening_kernel)
    
    blurred = cv.medianBlur(opened, 11)
    
    #------------ Black and White labeling ------------

    ret0, labels = cv.connectedComponents(blurred)

    numCells = np.max(np.max(labels));
    print("Number of cells:" + str(numCells))

    cells = np.zeros((numCells,H,W))

    most_left_pos = np.zeros(numCells)+W #Setting up for min finding
    most_top_pos = np.zeros(numCells)+H #Setting up for min finding
    most_right_pos = np.zeros(numCells) #Setting up for max finding
    most_bottom_pos = np.zeros(numCells) #Setting up for max finding
    

    for i in range(W):
      for j in range(H):
        element = labels[j,i]
        if element !=0:
          element = element-1
          cells[element,j,i] = 1  #Filling the element-th cell's space with ones
          #print(most_bottom_pos[element])
          if i<most_left_pos[element]:  #Finding the most left pos of a cell
            most_left_pos[element]=i;
          if i>most_right_pos[element]: #Finding the most right pos of a cell
            most_right_pos[element]=i;
          if j<most_top_pos[element]:   #Finding the most top pos of a cell
            most_top_pos[element]=j;
          if j>most_bottom_pos[element]:#Finding the most bottom pos of a cell
            most_bottom_pos[element]=j;


    #------------ Frame on the cells ------------

    invalid_cells = []

    Framed_cells = []
    for element in range(numCells):
      if(((int(most_top_pos[element])-int(most_bottom_pos[element]))*(int(most_left_pos[element])-int(most_right_pos[element])))<10000 and
         ((int(most_top_pos[element])-int(most_bottom_pos[element]))*(int(most_left_pos[element])-int(most_right_pos[element])))>100):
        ()
      else:
        invalid_cells.append(element)
      Framed_cells.append(cells[element, int(most_top_pos[element]):int(most_bottom_pos[element]), int(most_left_pos[element]):int(most_right_pos[element])])
      

    #------------ Peeling ------------
    CentresImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR);
    PrevCentres = Centres
    Centres = []
    for element in range(numCells):
      if invalid_cells.count(element)==0:
        Current_center = peeling(Framed_cells[element])
        Current_center[0] += most_left_pos[element]
        Current_center[1] += most_top_pos[element]
        Centres.append(Current_center)
        CentresImage[
                     max([int(Current_center[1])-5,0]):
                     min([int(Current_center[1])+5,H]),
                     max([int(Current_center[0])-5,0]):
                     min([int(Current_center[0])+5,W])
                     ]=(255,0,255)

    #------------ Closest neighbour alignment ------------

    MovementsImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR);
    if np.size(PrevCentres) != 0:
      Ncentres = np.zeros_like(PrevCentres)
      for c1 in range(np.shape(PrevCentres)[0]):
        mindist = H*W
        for c2 in range(np.shape(Centres)[0]):
          dist = np.sqrt(np.power(PrevCentres[c1][0]-Centres[c2][0], 2)+np.power(PrevCentres[c1][1]-Centres[c2][1], 2)) 
          if(dist<mindist):
            mindist = dist
            Ncentres[c1] = Centres[c2]
      AllCentres.append(Ncentres)
      AllPrevCentres.append(PrevCentres)

    #------------ Drawing the center connections ------------  

    if np.size(PrevCentres) != 0:
      for c in range(np.shape(AllPrevCentres)[0]):
        for c2 in range(np.shape(AllCentres[c])[0]):
          if np.shape(AllPrevCentres)[0]>1:
            #defining the irrational cases
            if (np.power(AllCentres[c][c2][0]-AllPrevCentres[c][c2][0],2)+np.power(AllCentres[c][c2][1]-AllPrevCentres[c][c2][1],2))<movementlimit*movementlimit:
              cv.line(MovementsImage, tuple([int(i) for i in AllPrevCentres[c][c2]]), tuple([int(i) for i in AllCentres[c][c2]]), (0,255,0), 5)

    ############ Diploma

              if c == np.shape(AllPrevCentres)[0]-1:
                cellp = cellpoint()
                cellp.frame = FrameCounter
                cellp.posx = int(AllCentres[c][c2][0])
                cellp.posy = int(AllCentres[c][c2][1])

                matchingID = -1
                for c3 in range(np.shape(AllPaths)[0]):
                  if AllPaths[c3].frame == FrameCounter-1 and AllPrevCentres[c][c2][0] == AllPaths[c3].posx and AllPrevCentres[c][c2][1] == AllPaths[c3].posy:
                    matchingID = AllPaths[c3].id

                if matchingID ==-1:
                  cellp.id = NewCellID
                  NewCellID = NewCellID+1
                  cellp.prev_missing_point = True
                else:
                  cellp.id = matchingID
                  cellp.prev_missing_point = False

                AllPaths.append(cellp)

            else:
              #"marking" the irrational outliers with -1
              AllCentres[c][c2][0]=-1
              AllCentres[c][c2][1]=-1

    #------------ Marking open endings ------------  

    SingleCellImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR);

    for p1 in AllPaths:
      if p1.frame == FrameCounter-1:
        p1.open_ending = True
        for p2 in AllPaths:
          if p2.frame == FrameCounter:
            if p2.id == p1.id:
              p1.open_ending = False

    #------------ Connecting broken up paths ------------ 

    for p1 in AllPaths:
      for p2 in AllPaths:

        for Traceback in range(MaxTraceback):
          if p1.frame == FrameCounter-Traceback-1:
            if p2.frame == FrameCounter:
              if p1.id != p2.id and p2.prev_missing_point == True and p1.open_ending == True and np.power(p1.posx-p2.posx,2)+np.power(p1.posy-p2.posy,2)<np.power(MaxTracebackDist-Traceback*TracebackCooldown,2):
                p2.id = p1.id
                cv.line(MovementsImage, tuple([p1.posx,p1.posy]), tuple([p2.posx,p2.posy]), (255,0,255), 5)
                print(Traceback)

    #------------ Showing the marked paths ------------   

    for p1 in AllPaths:
      for p2 in AllPaths:

        IDcolor = 0
        for TrID in TrackedIDs:
          IDcolor = IDcolor+1
          if p1.id == TrID:
            if p2.frame-1 == p1.frame and p2.id == TrID:
              cv.line(SingleCellImage, tuple([p1.posx, p1.posy]), tuple([p2.posx, p2.posy]), (0+(IDcolor*37)%255,255,0+(IDcolor*29)%255), 8)


    ############ SAJAT VEGE
    
    #Video write
    #out_opened.write(cv.cvtColor(opened, cv.COLOR_GRAY2BGR))
    #out_tresholded.write(cv.cvtColor(tresh, cv.COLOR_GRAY2BGR))
    out_centres.write(CentresImage)
    out_movements.write(MovementsImage)
    out_single_cell.write(SingleCellImage)

    prvs = next1
    
    picture_number+=1
    
    ret, frame2 = cap.read()
    
    FrameCounter +=1

print("Run finished sucessfully")

cap.release()

#out_opened.release()
#out_tresholded.release()
out_centres.release()
out_movements.release()
out_single_cell.release()

cv.destroyAllWindows()


0
Number of cells:22
1
Number of cells:19
2
Number of cells:20
3
Number of cells:19
4
Number of cells:17
1
5
Number of cells:21
6
Number of cells:27
7
Number of cells:24
8
Number of cells:24
9
Number of cells:26
10
Number of cells:17
11
Number of cells:26
1
1
1
12
Number of cells:26
2
2
2
2
2
2
2
2
2
2
2
0
13
Number of cells:25
14
Number of cells:25
15
Number of cells:26
16
Number of cells:25
2
17
Number of cells:25
2
1
18
Number of cells:24
19
Number of cells:25
0
20
Number of cells:18
21
Number of cells:24
22
Number of cells:23
2
2
2
2
2
2
2
2
2
2
2
2
23
Number of cells:23
24
Number of cells:25
25
Number of cells:24
26
Number of cells:24
2
27
Number of cells:22
28
Number of cells:22
29
Number of cells:23
30
Number of cells:24
31
Number of cells:15
0
32
Number of cells:25
33
Number of cells:25
2
2
2
2
2
2
2
2
2
2
2
34
Number of cells:25
35
Number of cells:25
36
Number of cells:27
37
Number of cells:28
2
38
Number of cells:22
39
Number of cells:26
40
Number of cells:27
41
Number of cel

In [44]:
#Writing all the paths into a txt file

if os.path.exists(out_path+'v3trajectories.txt'):
  os.remove(out_path+'v3trajectories.txt')

OutTrajectoriesTxt = open(out_path+'v3trajectories.txt','w')
for p in AllPaths:
  OutTrajectoriesTxt.write(str(p.frame)+'\t'+str(p.id)+'\t'+str(p.posx)+'\t'+str(p.posy)+'\n')
OutTrajectoriesTxt.close()

print("Trajectories successfully written!")

Trajectories successfully written!
